In [1]:
import os
import numpy as np
import math
import time
import matplotlib.pyplot as plt
import multiprocessing
from os import walk
import keras
import pickle
from keras.models import Sequential
from keras.layers import Dense, Dropout, Flatten
from keras.layers import Conv1D, MaxPooling1D
from sklearn.metrics import classification_report
from sklearn.metrics import confusion_matrix

Using TensorFlow backend.


In [2]:
RESULTS_DIR = './cnn_results/'
label_map = {'Hold': 0, 'Buy': 1, 'Sell': 2}
label_map_reverse = {0:'Hold', 1:'Buy', 2:'Sell'}

In [3]:
def get_paths(filepath):
    dataset_paths = []
    labels_paths = []
    stock_names = []
    for (dirpath, dirnames, filenames) in walk(filepath):
        dataset_paths = [filepath + '/' + name for name in dirnames]
        labels_paths = [filepath + '/' + name for name in filenames if name != '.DS_Store']
        stock_names = [name.split('_')[0] for name in filenames if name != '.DS_Store']
        break
    dataset_paths.sort()
    labels_paths.sort()
    stock_names.sort()

    return dataset_paths, labels_paths, stock_names

In [4]:
def read_data(d_path, l_path, s_name):
    
    with open(d_path+'/data.pkl', 'rb') as f:
        dataset = pickle.load(f)
    
    labels = np.zeros(len(dataset))
    prices = np.zeros(len(dataset))
    dates = np.empty(len(dataset), dtype='datetime64[s]')
    with open(l_path, 'r') as f:
        for i, line in enumerate(f):
            info = line.strip().split(', ')
            dates[i] = np.datetime64(info[1])
            prices[i] = info[2]
            labels[i] = label_map[info[3]]

    return [dataset, dates, prices, labels]

In [5]:
def data_augmentation(X_data, Y_data):
    proportion = np.array([0.34, 0.33, 0.33])
    labels_ind = [np.where(Y_data == x)[0] for x in range(3)]
    labels_tot = math.ceil(max([labels_ind[x].shape[0] / proportion[x] for x in range(len(labels_ind))]))

    labels_num = (proportion * labels_tot).astype(int)
    labels = np.arange(labels_num.sum())
    
    l = Y_data.shape[0]
    for i in range(labels_num.shape[0]):
        additional_ind = np.random.choice(labels_ind[i], labels_num[i] - labels_ind[i].shape[0])
        r = l + additional_ind.shape[0]
        labels[l:r] = additional_ind
        l = r

    return X_data[labels], Y_data[labels]

In [6]:
def data_processing(dataset, labels, augmentation):
    if augmentation:
        dataset, labels = data_augmentation(dataset, labels)
    
    X_data = dataset if len(dataset.shape) == 3 else dataset.reshape(dataset.shape[0], dataset.shape[1], 1)
    Y_data = keras.utils.to_categorical(labels)
    input_shape = X_data.shape[1:]

    return X_data, Y_data, input_shape

In [7]:
def data_extraction(data, start_year, end_year, augmentation):
    r = np.argwhere((data[1] >= np.datetime64(str(start_year))) & (data[1] < np.datetime64(str(end_year))))
    s = r[0][0]
    e = r[-1][0]

    dataset = data[0][s:e+1]
    dates = data[1][s:e+1]
    prices = data[2][s:e+1]
    labels = data[3][s:e+1]

    return data_processing(dataset, labels, augmentation), dates, prices

In [8]:
def create_model(input_shape, num_classes):
    model = Sequential()
    model.add(Conv1D(32, kernel_size=(3),
                     activation='relu',
                     input_shape=input_shape))
    model.add(Conv1D(64, (3), activation='relu'))
    # model.add(MaxPooling1D(pool_size=(2, 2)))
    model.add(Dropout(0.25))
    model.add(Flatten())
    model.add(Dense(128, activation='relu'))
    model.add(Dropout(0.5))
    model.add(Dense(num_classes, activation='softmax'))

    return model

In [9]:
def train(model, X_train, Y_train, X_test, Y_test, batch_size, epochs):
    model.compile(loss=keras.losses.categorical_crossentropy,
                  optimizer=keras.optimizers.Adadelta(),
                  metrics=['accuracy'])

    history = model.fit(X_train, Y_train,
              batch_size=batch_size,
              epochs=epochs,
              verbose=1,
              validation_data=(X_test, Y_test))
    
    return history

In [10]:
def test(model, X_test, Y_test):
    score = model.evaluate(X_test, Y_test, verbose=0)
    return score

In [11]:
class Report:

    @staticmethod
    def write_confusion_and_classif(cmatrix, save_path, y_test, y_pred, debug=True):
        with open(save_path + "/confusion_m.txt", 'w') as file:
            out_str = "%5s %4s %4s %4s" % ("", label_map_reverse[0], label_map_reverse[1], label_map_reverse[2])
            file.write(out_str + '\n')
            if debug:
                    print(out_str)

            for i, row in enumerate(cmatrix):
                out_str = "%4s: %4d %4d %4d" % (label_map_reverse[i], row[0], row[1], row[2])
                file.write(out_str + '\n')
                if debug:
                    print(out_str)

        with open(save_path + '/report.txt', 'w') as f:
            f.write(classification_report(y_test, y_pred))
        
        return

    @staticmethod
    def save_training_graph(save_path, history):
        # summarize history for accuracy
        plt.plot(history.history['acc'])
        plt.plot(history.history['val_acc'])
        plt.title('model accuracy')
        plt.ylabel('accuracy')
        plt.xlabel('epoch')
        plt.legend(['train', 'test'], loc='upper left')
        plt.savefig(os.path.join(save_path, 'acc.png'))
        plt.clf()

        # summarize history for loss
        plt.plot(history.history['loss'])
        plt.plot(history.history['val_loss'])
        plt.title('model loss')
        plt.ylabel('loss')
        plt.xlabel('epoch')
        plt.legend(['train', 'test'], loc='upper left')
        plt.savefig(os.path.join(save_path, 'loss.png'))
        return 

In [12]:
def train_process(X_train, Y_train, X_test, Y_test, dates, prices, year, results_dict, epochs):
    
    model = create_model(input_shape, len(label_map))
    history = train(model, X_train, Y_train, X_test, Y_test, 1028, epochs=epochs)
    save_path = RESULTS_DIR + s_name + '/' + str(year)
    
    if not os.path.exists(save_path):
        os.makedirs(save_path)
    
    model.save_weights(save_path + '/model_weights.h5')
    
    score = test(model, X_test, Y_test)
    results_dict['test_results'] += [(score[0], score[1], X_test.shape[0])]

    Y_test = np.argmax(Y_test, axis=1) # Convert one-hot to index
    y_pred = model.predict_classes(X_test)
    
    conf_matrix_temp = confusion_matrix(Y_test, y_pred)
    Report.write_confusion_and_classif(conf_matrix_temp, save_path, Y_test, y_pred)

    results_dict['conf_matrix'] += conf_matrix_temp
    results_dict['Y_test_sum'] = np.append(results_dict['Y_test_sum'], Y_test)
    results_dict['y_pred_sum'] = np.append(results_dict['y_pred_sum'], y_pred)
    prediction_dict = results_dict['prediction']
    for date, price, pred in zip(dates, prices, y_pred):
        prediction_dict[date] = (price, pred)
    results_dict['prediction'] = prediction_dict
    
    Report.save_training_graph(save_path, history)
    Report.write_confusion_and_classif(results_dict['conf_matrix'], RESULTS_DIR, results_dict['Y_test_sum'], results_dict['y_pred_sum'])
    
    with open(RESULTS_DIR + 'results.txt', 'a') as f:
        f.write('Year: {}. Number of samples: {}. Loss: {}. Accuracy: {}.\n'.format(str(year), X_test.shape[0], score[0], score[1]))


In [13]:
class Financial_Evaluation:

    @staticmethod
    def simulate(prediction, stock_name, years_num):
        COMMISION = 1
        
        init_balance = 10000
        balance = init_balance
        bought_cnt = 0

        for date, pred in prediction.items():
            price = pred[0]
            action = label_map_reverse[pred[1]]
            
            if action == 'Buy' and bought_cnt == 0:
                bought_cnt = (balance - COMMISION) / price
                balance = 0
            
            if action == 'Sell' and bought_cnt > 0:
                balance = bought_cnt * price - COMMISION
                bought_cnt = 0

        if bought_cnt > 0:
            balance = bought_cnt * price - COMMISION
            bought_cnt = 0

        total_return = balance / init_balance
        annualized_return = total_return ** (1.0/years_num)

        total_return = (total_return - 1.0) * 100
        annualized_return = (annualized_return - 1.0) * 100

        print('Stock:', stock_name, 'Total return:', total_return, 'Annualized return:', annualized_return)
        with open(RESULTS_DIR + 'results.txt', 'a') as f:
            f.write('Total return: {:.2f} %. Annualized return: {:.2f} %.\n'.format(total_return, annualized_return))

        return total_return, annualized_return

In [17]:
with open('./test_results/results.txt', 'w') as f:
        f.write('')

results_dict = multiprocessing.Manager().dict()
results_dict['test_results'] = []
results_dict['Y_test_sum'] = np.array([])
results_dict['y_pred_sum'] = np.array([])
results_dict['conf_matrix'] = np.zeros((3, 3))
results_dict['prediction'] = {}
images_paths, labels_paths, stock_names = get_paths('./data')

for s_ind, (i_path, l_path, s_name) in enumerate(zip(images_paths, labels_paths, stock_names)):
    print("STOCK: %s" % s_name)
    with open(RESULTS_DIR + 'results.txt', 'a') as f:
            f.write('\nSTOCK: {}\n'.format(s_name))

    data = read_data(i_path, l_path, s_name)
    results_dict['prediction'] = {}

    start_year = 2007
    years_num = 10
    epochs = 200
    for i in range(years_num):
        print('Testing year: ' + str(start_year + i))

        (X_train, Y_train, input_shape), _, _ = data_extraction(data, (start_year - 5) + i, start_year + i, True)
        (X_test, Y_test, input_shape), dates, prices = data_extraction(data, start_year + i, (start_year + 1) + i, False)

        p = multiprocessing.Process(target=train_process, args=(X_train, Y_train, X_test, Y_test, dates, prices, 2002 + i, results_dict, epochs))
        p.start()
        p.join()


    total_return, annualized_return = Financial_Evaluation.simulate(results_dict['prediction'], s_name, years_num)


    # if s_ind == 0: # only one stock will be evaluated
    #     break

# printing results
num_samples = sum([x[2] for x in results_dict['test_results']])
total_loss = sum([x[0] * x[2] for x in results_dict['test_results']]) / num_samples
total_acc = sum([x[1] * x[2] for x in results_dict['test_results']]) / num_samples
with open(RESULTS_DIR + 'results.txt', 'a') as f:
    f.write('\nNumber of samples: {}. Total Loss: {}. Total accuracy: {}.\n'.format(num_samples, total_loss, total_acc))

STOCK: AAPL
Testing year: 2007
Train on 3273 samples, validate on 251 samples
Epoch 1/200
3273/3273 [==============================] - 2s 680us/step - loss: 1.0813 - acc: 0.3905 - val_loss: 1.1006 - val_acc: 0.0757
Epoch 2/200
3273/3273 [==============================] - 0s 20us/step - loss: 1.0558 - acc: 0.4497 - val_loss: 1.0822 - val_acc: 0.1394
Epoch 3/200
3273/3273 [==============================] - 0s 21us/step - loss: 1.0414 - acc: 0.4500 - val_loss: 1.0637 - val_acc: 0.1912
Epoch 4/200
3273/3273 [==============================] - 0s 21us/step - loss: 1.0347 - acc: 0.4641 - val_loss: 1.0346 - val_acc: 0.2669
Epoch 5/200
3273/3273 [==============================] - 0s 22us/step - loss: 1.0292 - acc: 0.4662 - val_loss: 1.0419 - val_acc: 0.2510
Epoch 6/200
3273/3273 [==============================] - 0s 21us/step - loss: 1.0239 - acc: 0.4748 - val_loss: 1.0339 - val_acc: 0.2948
Epoch 7/200
3273/3273 [==============================] - 0s 21us/step - loss: 1.0156 - acc: 0.4742 - val_

3273/3273 [==============================] - 0s 22us/step - loss: 0.7230 - acc: 0.6740 - val_loss: 0.7632 - val_acc: 0.6853
Epoch 61/200
3273/3273 [==============================] - 0s 21us/step - loss: 0.7506 - acc: 0.6343 - val_loss: 0.8571 - val_acc: 0.5697
Epoch 62/200
3273/3273 [==============================] - 0s 22us/step - loss: 0.7181 - acc: 0.6609 - val_loss: 0.8389 - val_acc: 0.6215
Epoch 63/200
3273/3273 [==============================] - 0s 21us/step - loss: 0.7069 - acc: 0.6688 - val_loss: 0.8023 - val_acc: 0.6215
Epoch 64/200
3273/3273 [==============================] - 0s 22us/step - loss: 0.7268 - acc: 0.6575 - val_loss: 0.7388 - val_acc: 0.6733
Epoch 65/200
3273/3273 [==============================] - 0s 22us/step - loss: 0.7085 - acc: 0.6621 - val_loss: 0.7223 - val_acc: 0.7171
Epoch 66/200
3273/3273 [==============================] - 0s 21us/step - loss: 0.7036 - acc: 0.6621 - val_loss: 0.8448 - val_acc: 0.6056
Epoch 67/200
3273/3273 [==============================

Epoch 120/200
3273/3273 [==============================] - 0s 19us/step - loss: 0.6213 - acc: 0.7116 - val_loss: 0.7159 - val_acc: 0.6135
Epoch 121/200
3273/3273 [==============================] - 0s 20us/step - loss: 0.6066 - acc: 0.7244 - val_loss: 0.7404 - val_acc: 0.5817
Epoch 122/200
3273/3273 [==============================] - 0s 19us/step - loss: 0.6100 - acc: 0.7211 - val_loss: 0.6808 - val_acc: 0.6335
Epoch 123/200
3273/3273 [==============================] - 0s 19us/step - loss: 0.6129 - acc: 0.7229 - val_loss: 0.6189 - val_acc: 0.6892
Epoch 124/200
3273/3273 [==============================] - 0s 19us/step - loss: 0.6379 - acc: 0.6960 - val_loss: 0.7600 - val_acc: 0.5936
Epoch 125/200
3273/3273 [==============================] - 0s 19us/step - loss: 0.6057 - acc: 0.7207 - val_loss: 0.7401 - val_acc: 0.5657
Epoch 126/200
3273/3273 [==============================] - 0s 21us/step - loss: 0.6123 - acc: 0.7241 - val_loss: 0.6833 - val_acc: 0.6653
Epoch 127/200
3273/3273 [=========

3273/3273 [==============================] - 0s 20us/step - loss: 0.5703 - acc: 0.7409 - val_loss: 0.6638 - val_acc: 0.6375
Epoch 180/200
3273/3273 [==============================] - 0s 19us/step - loss: 0.5657 - acc: 0.7467 - val_loss: 0.6144 - val_acc: 0.6574
Epoch 181/200
3273/3273 [==============================] - 0s 19us/step - loss: 0.5581 - acc: 0.7492 - val_loss: 0.6542 - val_acc: 0.6215
Epoch 182/200
3273/3273 [==============================] - 0s 19us/step - loss: 0.5668 - acc: 0.7485 - val_loss: 0.5850 - val_acc: 0.6892
Epoch 183/200
3273/3273 [==============================] - 0s 18us/step - loss: 0.5562 - acc: 0.7574 - val_loss: 0.6128 - val_acc: 0.6653
Epoch 184/200
3273/3273 [==============================] - 0s 19us/step - loss: 0.5641 - acc: 0.7479 - val_loss: 0.6805 - val_acc: 0.5896
Epoch 185/200
3273/3273 [==============================] - 0s 19us/step - loss: 0.5582 - acc: 0.7421 - val_loss: 0.6597 - val_acc: 0.6255
Epoch 186/200
3273/3273 [=======================

3294/3294 [==============================] - 0s 20us/step - loss: 0.8395 - acc: 0.5832 - val_loss: 1.0627 - val_acc: 0.2095
Epoch 38/200
3294/3294 [==============================] - 0s 23us/step - loss: 0.8595 - acc: 0.5750 - val_loss: 0.9902 - val_acc: 0.2451
Epoch 39/200
3294/3294 [==============================] - 0s 21us/step - loss: 0.8379 - acc: 0.5938 - val_loss: 0.9789 - val_acc: 0.2332
Epoch 40/200
3294/3294 [==============================] - 0s 20us/step - loss: 0.8228 - acc: 0.6020 - val_loss: 0.9753 - val_acc: 0.5850
Epoch 41/200
3294/3294 [==============================] - 0s 20us/step - loss: 0.8935 - acc: 0.5565 - val_loss: 1.0360 - val_acc: 0.2095
Epoch 42/200
3294/3294 [==============================] - 0s 20us/step - loss: 0.8121 - acc: 0.6217 - val_loss: 0.9621 - val_acc: 0.3439
Epoch 43/200
3294/3294 [==============================] - 0s 21us/step - loss: 0.7999 - acc: 0.6266 - val_loss: 0.9731 - val_acc: 0.3755
Epoch 44/200
3294/3294 [==============================

...

3279/3279 [==============================] - 0s 19us/step - loss: 0.7612 - acc: 0.6167 - val_loss: 1.0162 - val_acc: 0.3651
Epoch 130/200
3279/3279 [==============================] - 0s 19us/step - loss: 0.7529 - acc: 0.6139 - val_loss: 1.0366 - val_acc: 0.3175
Epoch 131/200
3279/3279 [==============================] - 0s 19us/step - loss: 0.7575 - acc: 0.6194 - val_loss: 1.0087 - val_acc: 0.3214
Epoch 132/200
3279/3279 [==============================] - 0s 19us/step - loss: 0.7599 - acc: 0.6167 - val_loss: 1.0008 - val_acc: 0.3214
Epoch 133/200
3279/3279 [==============================] - 0s 18us/step - loss: 0.7602 - acc: 0.6185 - val_loss: 1.0131 - val_acc: 0.3532
Epoch 134/200
3279/3279 [==============================] - 0s 19us/step - loss: 0.7537 - acc: 0.6170 - val_loss: 1.0046 - val_acc: 0.3373
Epoch 135/200
3279/3279 [==============================] - 0s 19us/step - loss: 0.7512 - acc: 0.6255 - val_loss: 1.0310 - val_acc: 0.3571
Epoch 136/200
3279/3279 [=======================

3279/3279 [==============================] - 0s 18us/step - loss: 0.7035 - acc: 0.6475 - val_loss: 1.0067 - val_acc: 0.3095
Epoch 189/200
3279/3279 [==============================] - 0s 19us/step - loss: 0.7048 - acc: 0.6462 - val_loss: 0.9874 - val_acc: 0.3254
Epoch 190/200
3279/3279 [==============================] - 0s 19us/step - loss: 0.6928 - acc: 0.6545 - val_loss: 0.9712 - val_acc: 0.3294
Epoch 191/200
3279/3279 [==============================] - 0s 19us/step - loss: 0.7121 - acc: 0.6389 - val_loss: 0.9914 - val_acc: 0.3135
Epoch 192/200
3279/3279 [==============================] - 0s 19us/step - loss: 0.7034 - acc: 0.6584 - val_loss: 1.0047 - val_acc: 0.2937
Epoch 193/200
3279/3279 [==============================] - 0s 19us/step - loss: 0.6932 - acc: 0.6493 - val_loss: 1.0280 - val_acc: 0.2937
Epoch 194/200
3279/3279 [==============================] - 0s 19us/step - loss: 0.7022 - acc: 0.6548 - val_loss: 1.0296 - val_acc: 0.2817
Epoch 195/200
3279/3279 [=======================

3258/3258 [==============================] - 0s 19us/step - loss: 1.0299 - acc: 0.4669 - val_loss: 1.0330 - val_acc: 0.3492
Epoch 47/200
3258/3258 [==============================] - 0s 19us/step - loss: 1.0299 - acc: 0.4616 - val_loss: 1.0462 - val_acc: 0.2063
Epoch 48/200
3258/3258 [==============================] - 0s 18us/step - loss: 1.0348 - acc: 0.4573 - val_loss: 1.0473 - val_acc: 0.3333
Epoch 49/200
3258/3258 [==============================] - 0s 18us/step - loss: 1.0260 - acc: 0.4687 - val_loss: 1.0355 - val_acc: 0.2500
Epoch 50/200
3258/3258 [==============================] - 0s 18us/step - loss: 1.0245 - acc: 0.4665 - val_loss: 1.0273 - val_acc: 0.1667
Epoch 51/200
3258/3258 [==============================] - 0s 19us/step - loss: 1.0251 - acc: 0.4758 - val_loss: 1.0366 - val_acc: 0.2659
Epoch 52/200
3258/3258 [==============================] - 0s 19us/step - loss: 1.0250 - acc: 0.4601 - val_loss: 1.0313 - val_acc: 0.3095
Epoch 53/200
3258/3258 [==============================

Epoch 106/200
3258/3258 [==============================] - 0s 19us/step - loss: 0.8550 - acc: 0.5887 - val_loss: 0.9393 - val_acc: 0.5040
Epoch 107/200
3258/3258 [==============================] - 0s 19us/step - loss: 0.8598 - acc: 0.5850 - val_loss: 0.9897 - val_acc: 0.3175
Epoch 108/200
3258/3258 [==============================] - 0s 18us/step - loss: 0.8486 - acc: 0.5948 - val_loss: 0.9241 - val_acc: 0.5873
Epoch 109/200
3258/3258 [==============================] - 0s 19us/step - loss: 0.8600 - acc: 0.5810 - val_loss: 0.9341 - val_acc: 0.4167
Epoch 110/200
3258/3258 [==============================] - 0s 19us/step - loss: 0.8293 - acc: 0.6001 - val_loss: 0.9609 - val_acc: 0.3968
Epoch 111/200
3258/3258 [==============================] - 0s 19us/step - loss: 0.8316 - acc: 0.6007 - val_loss: 0.9246 - val_acc: 0.4365
Epoch 112/200
3258/3258 [==============================] - 0s 19us/step - loss: 0.8276 - acc: 0.6062 - val_loss: 0.9386 - val_acc: 0.4722
Epoch 113/200
3258/3258 [=========

3258/3258 [==============================] - 0s 19us/step - loss: 0.7144 - acc: 0.6366 - val_loss: 0.8707 - val_acc: 0.4206
Epoch 166/200
3258/3258 [==============================] - 0s 19us/step - loss: 0.7217 - acc: 0.6304 - val_loss: 0.8978 - val_acc: 0.4087
Epoch 167/200
3258/3258 [==============================] - 0s 19us/step - loss: 0.7125 - acc: 0.6418 - val_loss: 0.8809 - val_acc: 0.4286
Epoch 168/200
3258/3258 [==============================] - 0s 19us/step - loss: 0.7159 - acc: 0.6246 - val_loss: 0.9064 - val_acc: 0.4087
Epoch 169/200
3258/3258 [==============================] - 0s 19us/step - loss: 0.7181 - acc: 0.6378 - val_loss: 0.9346 - val_acc: 0.3929
Epoch 170/200
3258/3258 [==============================] - 0s 19us/step - loss: 0.7085 - acc: 0.6409 - val_loss: 0.9027 - val_acc: 0.4246
Epoch 171/200
3258/3258 [==============================] - 0s 19us/step - loss: 0.7081 - acc: 0.6415 - val_loss: 0.8923 - val_acc: 0.4167
Epoch 172/200
3258/3258 [=======================